# Sujet 3 : L'épidémie de choléra à Londres en 1854

À partir des données numériques, réalisez une carte dans l'esprit de celle de John Snow. Montrez les lieux de décès avec des symboles dont la taille indique le nombre de décès. Indiquez sur la même carte la localisation des pompes en utilisant une autre couleur et/ou un autre symbole. 

## Installation les packages nécessaires 
- package folium pour afficager la carte
- package geopandas pour lire les données 

Ce processus d'installation prendra certain minutes.

In [3]:
import sys
!{sys.executable} -m pip install folium
!{sys.executable} -m pip install geopandas  

     |████████████████████████████████| 94 kB 6.6 MB/s  eta 0:00:01
     |████████████████████████████████| 994 kB 6.0 MB/s eta 0:00:01
     |████████████████████████████████| 15.4 MB 18.6 MB/s eta 0:00:01
     |████████████████████████████████| 6.5 MB 24.1 MB/s eta 0:00:01
     |████████████████████████████████| 9.5 MB 62.1 MB/s eta 0:00:01
     |████████████████████████████████| 1.0 MB 29.2 MB/s eta 0:00:01
     |████████████████████████████████| 97 kB 8.7 MB/s  eta 0:00:01
     |████████████████████████████████| 14.8 MB 59.1 MB/s eta 0:00:01
  Attempting uninstall: numpy
    Found existing installation: numpy 1.15.2
    Uninstalling numpy-1.15.2:
      Successfully uninstalled numpy-1.15.2
  Attempting uninstall: pandas
    Found existing installation: pandas 0.22.0
    Uninstalling pandas-0.22.0:
      Successfully uninstalled pandas-0.22.0


## 1 Récupérer des données
Récupérer les données de [Snow](https://johnsnowsociety.org/) dans le webset [ici](http://blog.rtwilson.com/john-snows-cholera-data-in-more-formats/), les données incluent l'information de pompes et les détails des morts. 
 - fichier 'cholera_deaths.kml' inclut la position des morts et le nombre correspondant
 - fichier 'pumps.kml' inclut la position des pompes

In [4]:
import requests
import zipfile
import io

In [34]:
# Télécharge les données
# données de la format KML
zip_url = 'http://rtwilson.com/downloads/SnowGIS_KML.zip'

r = requests.get(zip_url)
z = zipfile.ZipFile(io.BytesIO(r.content))
z.extractall(path='./')

In [4]:
import geopandas as gpd
import fiona

#Extraire les données des morts et le nombre correspondant
gpd.io.file.fiona.drvsupport.supported_drivers['KML'] = 'rw'
df = gpd.read_file('SnowGIS_KML/cholera_deaths.kml', driver='KML')

le nombre de mort peut être trouvé dans l'information 'Description' 

In [5]:
df

Name                                        Description  \
0         <div class="googft-info-window" style="font-fa...   
1         <div class="googft-info-window" style="font-fa...   
2         <div class="googft-info-window" style="font-fa...   
3         <div class="googft-info-window" style="font-fa...   
4         <div class="googft-info-window" style="font-fa...   
..   ...                                                ...   
245       <div class="googft-info-window" style="font-fa...   
246       <div class="googft-info-window" style="font-fa...   
247       <div class="googft-info-window" style="font-fa...   
248       <div class="googft-info-window" style="font-fa...   
249       <div class="googft-info-window" style="font-fa...   

                      geometry  
0    POINT (-0.13793 51.51342)  
1    POINT (-0.13788 51.51336)  
2    POINT (-0.13785 51.51332)  
3    POINT (-0.13781 51.51326)  
4    POINT (-0.13777 51.51320)  
..                         ...  
245  POINT (-0.13711 51.51453)  
246  POINT (-0.13706 51.51471)  
247  POINT (-0.13847 51.51231)  
248  POINT (-0.13812 51.51200)  
249  POINT (-0.13776 51.51186)  

[250 rows x 3 columns]

In [6]:
#Extraire les données des pompes
pumpsdf = gpd.read_file('SnowGIS_KML/pumps.kml', driver='KML')
pumpsdf

Name                                        Description  \
0       <div class="googft-info-window" style="font-fa...   
1       <div class="googft-info-window" style="font-fa...   
2       <div class="googft-info-window" style="font-fa...   
3       <div class="googft-info-window" style="font-fa...   
4       <div class="googft-info-window" style="font-fa...   
5       <div class="googft-info-window" style="font-fa...   
6       <div class="googft-info-window" style="font-fa...   
7       <div class="googft-info-window" style="font-fa...   

                    geometry  
0  POINT (-0.13667 51.51334)  
1  POINT (-0.13959 51.51388)  
2  POINT (-0.13967 51.51491)  
3  POINT (-0.13163 51.51235)  
4  POINT (-0.13359 51.51214)  
5  POINT (-0.13592 51.51154)  
6  POINT (-0.13396 51.51002)  
7  POINT (-0.13820 51.51129)

## 2 Créer une carte de Londres 
Trouver la position de [Broad Street](https://fr.wikipedia.org/wiki/%C3%89pid%C3%A9mie_de_chol%C3%A9ra_de_Broad_Street), est changer la coordonnées à value de folium qui est [51.51323855699922, -0.13695845651105376] , et le donne à folium pour créer une carte de Londres.

In [15]:
import folium

m = folium.Map(location=[51.51323855699922, -0.13695845651105376],  zoom_start=17)  

In [16]:
# Afficher les pompes sur la carte
for index, row in pumpsdf.iterrows():
    folium.Marker(
        location=[row['geometry'].coords[0][1], row['geometry'].coords[0][0]],
        icon=folium.Icon(color='blue', icon='tint', prefix='glyphicon'),  #fas fa-faucet
        ).add_to(m)

In [17]:
# Afficher les morte sur la carte
for index, row in df.iterrows():
    folium.CircleMarker(
        location=[row['geometry'].coords[0][1], row['geometry'].coords[0][0]],
        radius=int(row['Description'][row['Description'].rfind('count:</b>')+10:row['Description'].rfind('</div>')]),
        popup='Count:' + row['Description'][row['Description'].rfind('count:</b>')+10:row['Description'].rfind('</div>')],
        color= 'red',
        weight = 2,
        fill=True,
        fill_color='red',
        fillOpacity=0,
        ).add_to(m)

 - la taille de la cercle rouge indique le nombre de décès, cliquez sur la zone du cercle rouge avec la souris pour afficher le nombre spécifique de décès à cet endroit.

 - Mark blue avec l'icône de gouttte d'eau indique la position des pompes.

In [19]:
m.save("mapBroadStreet1.html")
m

Résultat:

La carte nous montre que la distribution du cercle rouge est concentrée autour de la position de pomp de 'Broadwick Street', et la position qui a le plus grand nombre de morts de 15 personnes est proche de la position de pomp de 'Broadwick Street' aussi.

## 3 Méthode de densité des décès 
l'autres façons pour montrer que la pompe de Broad Street est au centre de l'épidémie. 

Calculer la densité des décès dans le quartier et l'afficher sur la carte. D'ici on calcul le nombre de morts à moins de 100 mètres de chaque pomp, et les affichons sur la carte.

La couleur rouge indique le nombre de morts est grand, par contre la couleur blue indique le nombre de morts est petit.

In [11]:
import math

#La fonction pour calcul la distance avec le coordonnées de la carte
# code source reference 
#https://instrovate.com/2019/07/01/tagging-two-locations-on-map-using-python-and-finding-distance-between-two-tagged-location-in-python/

def find_distance(origin, destination):
    lat1, lon1 = origin
    lat2, lon2 = destination
    radius = 6371 # km

    dlat = math.radians(lat2-lat1)
    dlon = math.radians(lon2-lon1)
    a = math.sin(dlat/2) * math.sin(dlat/2) + math.cos(math.radians(lat1)) \
        * math.cos(math.radians(lat2)) * math.sin(dlon/2) * math.sin(dlon/2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    distance_bw_ori_desti = radius * c
    return distance_bw_ori_desti


In [21]:
import folium
from folium.plugins import HeatMap

m = folium.Map(location=[51.51323855699922, -0.13695845651105376],  zoom_start=16)  

countList = []
for index, row in pumpsdf.iterrows():
    count = 0
    for i, dfrow in df.iterrows():
        dis = find_distance((dfrow['geometry'].coords[0][1],dfrow['geometry'].coords[0][0]),(row['geometry'].coords[0][1],row['geometry'].coords[0][0]))
        
        if dis*1000 < 100:
            count = count + int(dfrow['Description'][dfrow['Description'].rfind('count:</b>')+10:dfrow['Description'].rfind('</div>')])
    countList.append((row['geometry'].coords[0][1], row['geometry'].coords[0][0], count))
    '''
    folium.Circle(
        location=[row['geometry'].coords[0][1], row['geometry'].coords[0][0]],
        radius=100,
        popup=str(count),
        title=str(count),
        color= 'blue',
        weight = 6,
        opacity = count/100,
        fill=True,
        #fill_color='blue',
        fillOpacity=0,
        ).add_to(m)
    '''
    folium.Marker(
        location=[row['geometry'].coords[0][1], row['geometry'].coords[0][0]],
        popup=str(count),
        icon=folium.Icon(color='blue', icon='tint', prefix='glyphicon'),
        ).add_to(m)

    m.add_child(HeatMap(countList, radius=100))

In [22]:
m.save("mapBroadStreet2.html")
m

Résultat:

La carte nous montre que à côte de la position de pomp de 'Broadwick Street', la couleur de la région est plus rouge qu'il indique le nombre de morts est plus grand.
